# Goal: Recreate Gapminder's Bubble Chart*

![Gapminder](Gapminder.png)

*As much as possible...

See https://www.gapminder.org/tools/

## Import libraries

In [ ]:
import pandas as pd
import plotly.express as px
import plotly.graph_objs as go

## Load the data

In [ ]:
df = pd.read_csv('Gapminder-data.csv', sep=',')

In [ ]:
df.head()

In [ ]:
df.describe()

In [ ]:
df_info = pd.read_csv('Gapminder-info.csv', sep=',', index_col=0)

In [ ]:
df_info

In [ ]:
df = df.sort_values(['Year', 'Population'], ascending=[True, False])

In [ ]:
df.head()

## Create the bubble chart

In [ ]:
color_map = dict(
    Asia='#ff798e', 
    Europe='#ffeb33', 
    Africa='#33dded',
    Americas='#98ef33'
)
marker_dict = dict(
    opacity=1,
    line=dict(
        color='black',
        width=0.8
    )
)
layout_dict = dict(
    plot_bgcolor='white',
    font=dict(color='dimgray')
)
axes_dict = dict(
    gridcolor='lightgray',
    showline=True,
    linecolor='dimgray',
    linewidth=1,
    showspikes=True,
    spikethickness=1,
    spikecolor='dimgray'
)

In [ ]:
fig = px.scatter(
    df.query('Year==2020'),
    x='Income',
    y='Life expectancy',
    color='Region',
    size='Population',
    hover_name='Country',
    color_discrete_map=color_map,
    size_max=60,
    log_x=True,
    hover_data={c: False for c in df.columns},
    title='Gapminder<br><sup>Data by gapminder.org, CC-BY license</sup>'
)
# Adjust markers
fig.update_traces(marker=marker_dict)
# Adjust figure layout
fig.update_layout(layout_dict)
# Adjust axes/grid
fig.update_xaxes(axes_dict)
fig.update_yaxes(axes_dict)
fig.show()

## Add animation

In [ ]:
color_map = dict(
    Asia='#ff798e', 
    Europe='#ffeb33', 
    Africa='#33dded',
    Americas='#98ef33'
)
marker_dict = dict(
    opacity=1,
    line=dict(
        color='black',
        width=0.8
    )
)
layout_dict = dict(
    plot_bgcolor='white',
    font=dict(color='dimgray'),
    autosize=False,
    width=800,
    height=600,
    clickmode='event+select'
)
axes_dict = dict(
    gridcolor='lightgray',
    showline=True,
    linecolor='dimgray',
    linewidth=1,
    showspikes=True,
    spikethickness=1,
    spikecolor='dimgray'
)

In [ ]:
def background_year(year, xaxis, yaxis):
    return dict(
        x=[df_info.loc[xaxis, 'Mid']],
        y=[df_info.loc[yaxis, 'Mid']],
        mode='text',
        text=[str(year)],
        showlegend=False,
        textfont=dict(size=200, color='lightgray'),
        textposition='middle center'
    )

In [ ]:
def gapminder_fig(xaxis='Income', yaxis='Life expectancy'):
    fig = px.scatter(
        df.query('Year>=2010'),
        x=xaxis,
        y=yaxis,
        color='Region',
        size='Population',
        hover_name='Country',
        color_discrete_map=color_map,
        size_max=60,
        log_x=df_info.loc[xaxis, 'LogScale'],
        log_y=df_info.loc[yaxis, 'LogScale'],
        hover_data={c: False for c in df.columns},
        title='Gapminder<br><sup>Data by gapminder.org, CC-BY license</sup>',
        animation_frame='Year',
        animation_group='Country',
        range_x=[df_info.loc[xaxis, 'Min'], df_info.loc[xaxis, 'Max']],
        range_y=[df_info.loc[yaxis, 'Min'], df_info.loc[yaxis, 'Max']]
    )
    # Adjust markers
    fig.update_traces(marker=marker_dict)
    # Adjust figure layout
    fig.update_layout(layout_dict)
    # Adjust axes/grid
    fig.update_xaxes(axes_dict)
    fig.update_yaxes(axes_dict)

    # Show the year in the background
    frame_year = fig.frames[0].name
    fig.add_trace(go.Scatter(background_year(frame_year, xaxis, yaxis)))
    fig.data = (fig.data[-1], ) + fig.data[:-1]
    
    for frame in fig.frames:
        frame.data =  (background_year(frame.name, xaxis, yaxis), ) + frame.data
    fig.update(frames=fig.frames)

    # Add annotations to the axes
    fig.add_annotation(
        x=1, y=0, xref='x domain', yref='y domain',
        text=df_info.loc[xaxis, 'Meaning'],
        showarrow=False, align='right'
    )
    fig.add_annotation(
        x=0, y=1, xref='x domain', yref='y domain',
        text=df_info.loc[yaxis, 'Meaning'],
        showarrow=False, valign='top', textangle=-90
    )
    
    return fig
    
fig = gapminder_fig(yaxis='Fertility')
fig.show()

## Use Dash

- Dash html components: https://dash.plotly.com/dash-html-components
- Dash core components: https://dash.plotly.com/dash-core-components

In [ ]:
from dash import Dash, html, dcc, callback, Output, Input

In [ ]:
import json

In [ ]:
attributes = ['Income', 'Life expectancy', 'Fertility', 'Child mortality']
external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']
app = Dash(__name__, external_stylesheets=external_stylesheets)

In [ ]:
app.layout = html.Div([
    html.H1('Interactive data visualization', 
            style={'fontSize': 50, 'color': 'brown'}),
    html.P('X axis'),
    dcc.Dropdown(
        id='dropdown_x',
        options=[{'label': a, 'value': a} for a in attributes],
        value='Income'
    ),
    html.P('Y axis'),
    dcc.Dropdown(
        id='dropdown_y',
        options=[{'label': a, 'value': a} for a in attributes],
        value='Life expectancy'
    ),
    dcc.Graph(
        id='plot',
        figure=gapminder_fig()
    ),
    dcc.Textarea(
        id='text',
        value=''
    )
])

@app.callback(
    Output('plot', 'figure'),
    [Input('dropdown_x', 'value'), Input('dropdown_y', 'value')]
)
def update_plot(x, y):
    return gapminder_fig(x, y)

@app.callback(
    Output('text', 'value'),
    Input('plot', 'selectedData')
)
def print_value(selected_data):
    return json.dumps(selected_data, indent=2)

In [ ]:
app.run()